# *MunchXMLmuncher* Alpha
Developed by research assistant Loke Sjølie for the University of Oslo
___
Users:
I ask that you do not touch anything under the header **Program** unless you *sort of* know what you're doing. :)

Developers:
I apologize in advance.
## Options

In [26]:
# Users: only edit things that exist WITHIN double quotation marks ("").
newtitle = "MunchXMLmuncher Alpha Test Result" # Title of resulting CMIF
editorName = "Loke Sjølie" # The name to issue to the CMIF file as "editor" (responsible for this file)
editorMail = "loke.sjolie@ub.uio.no" # The e-mail associated with the above.

version = "0.2" # Describes the "program's" state of completion and versioning.
cmifUid = "a403c593-09df-4538-8acf-8d459339fca8" # Unique ID. Used in sourceDesc of CMIF. Don't change it without a good reason.

inputfilepath = r"INPUT/tei.xml" # Where is the target TEI source file located?

## Program

### Init, metadata, etc

In [82]:
from bs4 import BeautifulSoup # Hent BeautifulSoup-modulen (https://www.crummy.com/software/BeautifulSoup/) for XML
from bs4 import Comment # BS4-addon for å håndtere kommentarer <!-- X -->
from datetime import date # Dates
import time # Time
import re # Regex
#import glob # The yeast of thought and mind
#import os # Filsystem for lasting og lagring
today = date.today() # Sett dato i dag
today = today.strftime("%Y-%m-%d") # Formater dato
currVer = version+" "+today

In [32]:
previouslyRun = "Last executed code was version "+str(version)+" on date "+str(today)+". All OUTPUT files are current to that version on that date.\n"+str(cmifUid)+"."
print("Version",currVer)
try:
    with open(r"settings/previous", "r") as file: # Åpne filen med encoding UTF8
        f = file.readlines() # Les innholdet som linjer
        f = "".join(f) # Linjene blir kombinert i en variabel
    if f == previouslyRun:
        print("> Re-run detected. If you've changed anything, make sure to update the version var.")
    else:
        f = open(r"settings/previous", "w")
        f.write(previouslyRun)
        print("> Updated internal files to reflect the date and version we're running today.")
    file.close()
except:
    f = open(r"settings/previous", "w")
    f.write(previouslyRun)
    f.close()
    print("> I made a new file to keep track of when the script was last run.")

Version 0.2 2022-08-18
> Updated internal files to reflect the date and version we're running today.


### Read/process TEI-XML

In [33]:
with open(inputfilepath, "r", encoding="utf-8") as file: # Open a file
    tei = file.readlines() # Les innholdet som linjer
    tei = "".join(tei) # Linjene blir kombinert i en variabel
soup = BeautifulSoup(tei, from_encoding="UTF-8") # It is now soup

#### Debug stuff - Tags/attributes
What is this thing? An investigation of the input document's tags.

In [34]:
tagsAttrs = [] # New list
for x in soup.findAll(): # For every tag in the soup
    tag = str(x.name) # Assign name of tag to var tag
    for attribute in x.attrs: # For every attribute belonging to the tag
        tag = tag+" @"+attribute # Append attribute to tag with " @" as separator - results in combination
    if tag not in tagsAttrs: # If this particular combination of tag/attribute(s) has not been seen previously
        tagsAttrs.append(tag) # Register it in our list
# Dict with known tag/attribute pairings and understood meanings
dict = {
    "tei":"The TEI element - is where our file actually begins.",
    "teiheader":"The TEI header contains metadata (titleStmt, publicationStmt, sourceDesc...).",
    "p":"P is a paragraph. This is used in the TEIheader to contain the actual strings for publication & source desc. And a single, random </p> element later.",
    "body":"Body is used as a sub-element of <text> to contain all the metadata for all letters. I am personally offended by this practice. BS4 adds one, too.",
    "text":"Text appears to be a wrapper for the body tag, which contains all the texts' metadata.",
    "div":"Div, with @xml:id, is used to contain the metadata of a single letter.",
    "date":"Date is a date element. It seems to have the @when attribute very often, as well as enclosed text. Often has @type(year/fromTo, etc.)",
    "table":"Table is the primary data structure in which information about each letter is stored. This is a *table*.",
    "row":"Row is a sub-element of the table element. It defines a new X-axis in a table.",
    "seg":"Seg appears to be some kind of ID attached to each letter. The ID is used as an @xml:id attribute in div, and the element appears in references to other letters.",
    "cell":"Cell is a sub-element of the table element also. A single cell appears to be an entry into a row element.",
    "ref":"Ref appears to contain references to other XML items.",
    "item":"Item is a generic element that has multiple @attributes, such as owner, owner signature, author, paper type... This is evidently a very important tag.",
    "list":"List is a list. Often, the list only has one item. The list is used as description tag, containing other lists, and describes anything between dates to material type.",
    "html":"The HTML tag can be ignored. BS4 adds this.",
    "filedesc":"Filedesc contains title, publication, source statements.",
    "sourcedesc":"Sourcedesc describes the source of the whole document.",
    "publicationstmt":"Publication statement for the whole document.",
    "title":"Title for the whole document.",
    "titlestmt":"Titlestmt is a wrapper for the title tag (whole document).",
    "div @xml:id":"Div has an attribute @xml:id. This describes the unique ID of the item in question.",
    "list @type":"List's @type attribute describes whether the list is wrapped around an object/physical description, a date, or other category.",
    "item @n":"Item's @n attribute describes role, library sorting, language, measures, dated, notes and so on. Very... multipurpose.",
    "tei @xmlns @xml:id":"tei @xmlns @xml:id is functionally identical to TEI tag. Just the one.",
    "date @type @from @to":"date @type @from @to describes the sequence type=fromTo, from, to. A date range.",
    "ref @target":"ref's @target attribute describes a URL to another XML.",
    "date @type @when":"Date with attributes type and when. Single date/year.",
    "ref @type @target":"Seems to contain URL to eMunch's web pages for a 'Read More' function.",
    "date @type @from":"date @type @from is an open-ended date.",
    "date @type":"Caution: date @type is a date with just a type. The date itself might be enclosed...? Potentially misleading. Investigate.",
    "ref @target @n":"ref @target @n - like ref @target, but @n tends to be the name of an institution or so.",
    "row @n":"row @n describes parts of the text. Inventory number, paper type, etc.",
    "ref @type @target @n":"ref @type @target @n - Working off of previous information, I'll infer that ref @type @target @n describes a Read More, with URL, with name."
}
print("Listing all unique tags and attribute combinations found with mapped, understood meanings.\n")
tagsAttrs.sort() # We do a little sorting
for x in tagsAttrs: # For every tag/attr combination registered
    if x in dict: # If our dict has the combo
        if "@" in x: # If there's an attribute involved
            print("ATTR ["+str(x)+"]",dict[x]) # Print with attribute focus
        else: # If there is no attribute involved
            print("TAG ["+str(x)+"]",dict[x]) # Print with tag focus
    else: # If our dict does not have the combo
        print("\n"+str(x),"has no description. What is this?\n") # Print error
comments = soup.find_all(string=lambda text: isinstance(text, Comment)) # Find all comments in soup
if comments: # If there are comments
    n = len(comments) # Check how many comments
    print("\n> Detected",n,"comments (<!-- -->, etc). These should be eradicated before tag extraction.") # Print message
else: # If there are no comments
    print("\n> There are no (0) comments to worry about in this document.") # There are no comments

Listing all unique tags and attribute combinations found with mapped, understood meanings.

TAG [body] Body is used as a sub-element of <text> to contain all the metadata for all letters. I am personally offended by this practice. BS4 adds one, too.
TAG [cell] Cell is a sub-element of the table element also. A single cell appears to be an entry into a row element.
TAG [date] Date is a date element. It seems to have the @when attribute very often, as well as enclosed text. Often has @type(year/fromTo, etc.)
ATTR [date @type] Caution: date @type is a date with just a type. The date itself might be enclosed...? Potentially misleading. Investigate.
ATTR [date @type @from] date @type @from is an open-ended date.
ATTR [date @type @from @to] date @type @from @to describes the sequence type=fromTo, from, to. A date range.
ATTR [date @type @when] Date with attributes type and when. Single date/year.
TAG [div] Div, with @xml:id, is used to contain the metadata of a single letter.
ATTR [div @xml:

We have notes as well as letters. The notes generally do not have a item @recipient tag, while the letters generally do.

Every div has an xml:id, and an enclosed ID.

Every item then has a list with items in it.

#### Debug stuff - Types of attributes
There's a whole lot of item *n* tags. What are they? Let's find out. The following extracts list and item tags with unique attribute texts. We have to filter out a loooot of tags that're IDs, dates etc. And look - we got cells, too!

In [35]:
itemNs = []
itemXmlIds = []
itemDates = []
itemTargets = []
lists = itemNs,itemXmlIds,itemDates,itemTargets
for x in soup.findAll(True):
    name = x.name
    if "list" in name:
        children = x.findChildren(True, recursive=True)
        i=0
        for child in children:
            if len(child.attrs) == 0:
                print("Child of",name,i,child.name,"\n")
            else:
                print("Child of",name,i,child.name,child.attrs,"\n")
            i+=1
    for i in x.attrs:
        attribute = i
        value = x.attrs[i]
        try:
            contents = x.contents[0]
            fullTag = str(name)+" @"+str(attribute)+" = "+str(value)+" "+str(contents)
        except:
            fullTag = str(name)+" @"+str(attribute)+ "= "+str(value)
        if "@xml:id" in fullTag:
            if fullTag not in itemXmlIds:
                itemXmlIds.append(fullTag)
        elif "date" in fullTag:
            if fullTag not in itemDates:
                itemDates.append(fullTag)
        elif "@target" in fullTag:
            if fullTag not in itemTargets:
                itemTargets.append(fullTag)   
        else:
            if fullTag not in itemNs:
                itemNs.append(fullTag)
#for x in lists:
#    x.sort()
#itemNs

Child of list 0 item {'n': 'ownerMsSig'} 

Child of list 1 item {'n': 'owner'} 

Child of list 0 item {'n': 'author'} 

Child of list 1 item 

Child of list 2 list {'type': 'objectType'} 

Child of list 3 item {'n': 'notes'} 

Child of list 4 item 

Child of list 5 list {'type': 'date'} 

Child of list 6 item {'n': 'dated'} 

Child of list 7 date {'type': 'fromTo', 'from': '1889', 'to': '1890'} 

Child of list 8 item {'n': 'language'} 

Child of list 0 item {'n': 'notes'} 

Child of list 0 item {'n': 'dated'} 

Child of list 1 date {'type': 'fromTo', 'from': '1889', 'to': '1890'} 

Child of list 0 item {'n': 'paperType'} 

Child of list 1 item {'n': 'measures'} 

Child of list 0 item {'n': 'ownerMsSig'} 

Child of list 1 item {'n': 'owner'} 

Child of list 0 item {'n': 'author'} 

Child of list 1 item 

Child of list 2 list {'type': 'objectType'} 

Child of list 3 item {'n': 'notes'} 

Child of list 4 item 

Child of list 5 list {'type': 'date'} 

Child of list 6 item {'n': 'dated'} 



Child of list 0 item {'n': 'paperType'} 

Child of list 1 item {'n': 'measures'} 

Child of list 0 item {'n': 'textParts'} 

Child of list 1 table 

Child of list 2 row {'n': 'textPartNo'} 

Child of list 3 cell 

Child of list 4 cell 

Child of list 5 cell 

Child of list 0 item {'n': 'ownerMsSig'} 

Child of list 1 item {'n': 'owner'} 

Child of list 2 item {'n': 'altRegNo'} 

Child of list 0 item {'n': 'author'} 

Child of list 1 item 

Child of list 2 list {'type': 'objectType'} 

Child of list 3 item {'n': 'notes'} 

Child of list 4 item 

Child of list 5 list {'type': 'date'} 

Child of list 6 item {'n': 'dated'} 

Child of list 7 date {'type': 'fromTo', 'from': '1908', 'to': '1924'} 

Child of list 8 item {'n': 'language'} 

Child of list 0 item {'n': 'notes'} 

Child of list 0 item {'n': 'dated'} 

Child of list 1 date {'type': 'fromTo', 'from': '1908', 'to': '1924'} 

Child of list 0 item {'n': 'paperType'} 

Child of list 1 item {'n': 'measures'} 

Child of list 0 item {'n': 

Child of list 2 row {'n': 'textPartNo'} 

Child of list 3 cell 

Child of list 4 cell 

Child of list 5 cell 

Child of list 6 cell 

Child of list 0 item {'n': 'ownerMsSig'} 

Child of list 1 item {'n': 'owner'} 

Child of list 0 item {'n': 'author'} 

Child of list 1 item 

Child of list 2 list {'type': 'objectType'} 

Child of list 3 item {'n': 'notes'} 

Child of list 4 item 

Child of list 5 list {'type': 'date'} 

Child of list 6 item {'n': 'dated'} 

Child of list 7 date {'type': 'year', 'when': '1938'} 

Child of list 8 item {'n': 'language'} 

Child of list 0 item {'n': 'notes'} 

Child of list 0 item {'n': 'dated'} 

Child of list 1 date {'type': 'year', 'when': '1938'} 

Child of list 0 item {'n': 'paperType'} 

Child of list 1 item {'n': 'measures'} 

Child of list 0 item {'n': 'ownerMsSig'} 

Child of list 1 item {'n': 'owner'} 

Child of list 2 item {'n': 'altRegNo'} 

Child of list 0 item {'n': 'author'} 

Child of list 1 item 

Child of list 2 list {'type': 'objectType'

Child of list 1 item {'n': 'measures'} 

Child of list 0 item {'n': 'ownerMsSig'} 

Child of list 1 item {'n': 'owner'} 

Child of list 0 item {'n': 'author'} 

Child of list 1 item 

Child of list 2 list {'type': 'objectType'} 

Child of list 3 item {'n': 'notes'} 

Child of list 4 item 

Child of list 5 list {'type': 'date'} 

Child of list 6 item {'n': 'dated'} 

Child of list 7 date {'type': 'fromTo', 'from': '1930', 'to': '1935'} 

Child of list 8 item {'n': 'language'} 

Child of list 0 item {'n': 'notes'} 

Child of list 0 item {'n': 'dated'} 

Child of list 1 date {'type': 'fromTo', 'from': '1930', 'to': '1935'} 

Child of list 0 item {'n': 'paperType'} 

Child of list 1 item {'n': 'measures'} 

Child of list 0 item {'n': 'ownerMsSig'} 

Child of list 1 item {'n': 'owner'} 

Child of list 0 item {'n': 'author'} 

Child of list 1 item 

Child of list 2 list {'type': 'objectType'} 

Child of list 3 item {'n': 'notes'} 

Child of list 4 item 

Child of list 5 list {'type': 'date'}

Child of list 2 list {'type': 'objectType'} 

Child of list 3 item {'n': 'notes'} 

Child of list 4 item 

Child of list 5 list {'type': 'date'} 

Child of list 6 item {'n': 'dated'} 

Child of list 7 date {'type': 'year', 'when': '1939'} 

Child of list 8 item {'n': 'language'} 

Child of list 0 item {'n': 'notes'} 

Child of list 0 item {'n': 'dated'} 

Child of list 1 date {'type': 'year', 'when': '1939'} 

Child of list 0 item {'n': 'paperType'} 

Child of list 1 item {'n': 'measures'} 

Child of list 0 item {'n': 'ownerMsSig'} 

Child of list 1 item {'n': 'owner'} 

Child of list 0 item {'n': 'author'} 

Child of list 1 item 

Child of list 2 list {'type': 'objectType'} 

Child of list 3 item {'n': 'notes'} 

Child of list 4 item 

Child of list 5 list {'type': 'date'} 

Child of list 6 item {'n': 'dated'} 

Child of list 7 date {'type': 'year', 'when': '1934'} 

Child of list 8 item {'n': 'language'} 

Child of list 0 item {'n': 'notes'} 

Child of list 0 item {'n': 'dated'} 

Ch

...

Child of list 8 item {'n': 'philologicalComm'} 

Child of list 0 item {'n': 'notes'} 

Child of list 0 item {'n': 'undated'} 

Child of list 0 item {'n': 'paperType'} 

Child of list 0 item {'n': 'ownerMsSig'} 

Child of list 1 item {'n': 'owner'} 

Child of list 0 item {'n': 'author'} 

Child of list 1 item 

Child of list 2 list {'type': 'objectType'} 

Child of list 3 item {'n': 'notes'} 

Child of list 4 item 

Child of list 5 list {'type': 'date'} 

Child of list 6 item {'n': 'dated'} 

Child of list 7 date {'type': 'fromTo', 'from': '1875', 'to': '1876'} 

Child of list 8 item {'n': 'language'} 

Child of list 0 item {'n': 'notes'} 

Child of list 0 item {'n': 'dated'} 

Child of list 1 date {'type': 'fromTo', 'from': '1875', 'to': '1876'} 

Child of list 0 item {'n': 'paperType'} 

Child of list 0 item {'n': 'ownerMsSig'} 

Child of list 1 item {'n': 'owner'} 

Child of list 0 item {'n': 'author'} 

Child of list 1 item 

Child of list 2 list {'type': 'objectType'} 

Child of li

Child of list 1 item {'n': 'owner'} 

Child of list 0 item {'n': 'author'} 

Child of list 1 item {'n': 'recipient'} 

Child of list 2 ref {'target': 'person.xhtml?id=pe66'} 

Child of list 3 item {'n': 'sort'} 

Child of list 4 item 

Child of list 5 list {'type': 'objectType'} 

Child of list 6 item {'n': 'letter'} 

Child of list 7 item 

Child of list 8 list {'type': 'date'} 

Child of list 9 item {'n': 'dated'} 

Child of list 10 date {'type': 'fromTo', 'from': '1906', 'to': '1908'} 

Child of list 11 item {'n': 'language'} 

Child of list 0 item {'n': 'letter'} 

Child of list 0 item {'n': 'dated'} 

Child of list 1 date {'type': 'fromTo', 'from': '1906', 'to': '1908'} 

Child of list 0 item {'n': 'paperType'} 

Child of list 0 item {'n': 'ownerMsSig'} 

Child of list 1 item {'n': 'owner'} 

Child of list 0 item {'n': 'author'} 

Child of list 1 item {'n': 'recipient'} 

Child of list 2 ref {'target': 'person.xhtml?id=pe66'} 

Child of list 3 item {'n': 'sort'} 

Child of list 4 

Child of list 14 ref {'target': 'HYBRIDNo-MM_K2829.xhtml'} 

Child of list 0 item {'n': 'draft'} 

Child of list 0 item {'n': 'dated'} 

Child of list 1 date {'type': 'year', 'when': '1908'} 

Child of list 2 date {'type': 'month', 'when': '--07'} 

Child of list 0 item {'n': 'ownerMsSig'} 

Child of list 1 item {'n': 'owner'} 

Child of list 0 item {'n': 'author'} 

Child of list 1 item 

Child of list 2 list {'type': 'objectType'} 

Child of list 3 item {'n': 'notes'} 

Child of list 4 item 

Child of list 5 list {'type': 'date'} 

Child of list 6 item {'n': 'dated'} 

Child of list 7 date {'type': 'year', 'when': '1894'} 

Child of list 8 date {'type': 'month', 'when': '--12'} 

Child of list 9 item {'n': 'language'} 

Child of list 10 item {'n': 'philologicalComm'} 

Child of list 11 ref {'target': 'HYBRIDNo-MM_K2901.xhtml'} 

Child of list 0 item {'n': 'notes'} 

Child of list 0 item {'n': 'dated'} 

Child of list 1 date {'type': 'year', 'when': '1894'} 

Child of list 2 date {'ty

Child of list 5 list {'type': 'date'} 

Child of list 6 item {'n': 'dated'} 

Child of list 7 date {'type': 'year', 'when': '1930'} 

Child of list 8 date {'type': 'month', 'when': '--08'} 

Child of list 9 item {'n': 'language'} 

Child of list 10 item {'n': 'philologicalComm'} 

Child of list 11 ref {'target': 'HYBRIDNo-MM_I0480.xhtml'} 

Child of list 0 item {'n': 'notes'} 

Child of list 0 item {'n': 'dated'} 

Child of list 1 date {'type': 'year', 'when': '1930'} 

Child of list 2 date {'type': 'month', 'when': '--08'} 

Child of list 0 item {'n': 'ownerMsSig'} 

Child of list 1 item {'n': 'owner'} 

Child of list 0 item {'n': 'author'} 

Child of list 1 item 

Child of list 2 list {'type': 'objectType'} 

Child of list 3 item {'n': 'notes'} 

Child of list 4 item 

Child of list 5 list {'type': 'date'} 

Child of list 6 item {'n': 'dated'} 

Child of list 7 date {'type': 'year', 'when': '1943'} 

Child of list 8 item {'n': 'language'} 

Child of list 9 item {'n': 'philologicalCom

Child of list 4 item 

Child of list 5 list {'type': 'objectType'} 

Child of list 6 item {'n': 'draft'} 

Child of list 7 item 

Child of list 8 list {'type': 'date'} 

Child of list 9 item {'n': 'dated'} 

Child of list 10 date {'type': 'year', 'when': '1879'} 

Child of list 11 item {'n': 'language'} 

Child of list 0 item {'n': 'draft'} 

Child of list 0 item {'n': 'dated'} 

Child of list 1 date {'type': 'year', 'when': '1879'} 

Child of list 0 item {'n': 'ownerMsSig'} 

Child of list 1 item {'n': 'owner'} 

Child of list 0 item {'n': 'author'} 

Child of list 1 item {'n': 'recipient'} 

Child of list 2 ref {'target': 'institution.xhtml?id=i26', 'n': 'Göteborgs Konstmuseum'} 

Child of list 3 item 

Child of list 4 list {'type': 'objectType'} 

Child of list 5 item {'n': 'letter'} 

Child of list 6 item 

Child of list 7 list {'type': 'date'} 

Child of list 8 item {'n': 'dated'} 

Child of list 9 date {'type': 'year', 'from': '1912', 'to': '1913'} 

Child of list 10 item {'n': '

In [36]:
testSpace = soup.find("div")

children = testSpace.findChildren(True, recursive=True)
i=0

print("Parent <"+testSpace.name,list(child.attrs.keys())[0]+"=\""+list(testSpace.attrs.values())[0]+"\">")
documentID = "<correspDesc key=\""+list(testSpace.attrs.values())[0]+"\">"
documentUUID = "#"+str(cmifUid)
for child in children:
    u = 0
    if child.attrs:
        n = len(child.attrs)
        valuelist = list(child.attrs.values())[:n]
        keylist = list(child.attrs.keys())[:n]
        print("> Child",str(i)+" <"+str(child.name)+">")
        while u < n:
            print(">> "+str(keylist[u])+"=\""+str(valuelist[u])+"\"")
            u+=1
    else:
        print("> Child",i,child.name,"(no attributes)")
    i+=1
#testSpace


Parent <div n="No-MM_N0004">
> Child 0 <list>
>> type="proveniens"
> Child 1 <item>
>> n="ownerMsSig"
> Child 2 <item>
>> n="owner"
> Child 3 <list>
>> type="description"
> Child 4 <item>
>> n="author"
> Child 5 item (no attributes)
> Child 6 <list>
>> type="objectType"
> Child 7 <item>
>> n="notes"
> Child 8 item (no attributes)
> Child 9 <list>
>> type="date"
> Child 10 <item>
>> n="dated"
> Child 11 <date>
>> type="fromTo"
>> from="1889"
>> to="1890"
> Child 12 <item>
>> n="language"
> Child 13 <list>
>> type="physDescription"
> Child 14 <item>
>> n="paperType"
> Child 15 <item>
>> n="measures"


All comments destroyed.


In [105]:
# Before handling the data: remove all comments
# Making a list of <!--comments--> to be destroyed...
commentDocs = 0 # Used only in terminating comments
comments = 0 # Used only in terminating comments
start = time.time()

for comment in soup.findAll(string=lambda text: isinstance(text, Comment)):
    if "xml:id=\"" in comment:
        commentDocs+=1
    comment.extract()
    comments+=1
if comments > 0:
    print("Destroyed",comments,"<!--comments-->, of which",commentDocs,"contained an @XML:ID.")
# ... and checking it twice.
comments = soup.findAll(string=lambda text: isinstance(text, Comment))
if comments:
    print("There are still",len(comments),"comments present.")
else:
    print("All comments destroyed.")

    # Declare variables
# ---------------------------------------------------------------
errors_found = [] # List of errors found during execution
letterCount = 0 # # letters, as defined by an item having a recipient, processed
miscCount = 0 # non-letter documents, as defined by an item having no recipients, processed
addresseesUnique = [] # List of unique recipients
# ---------------------------------------------------------------

# Limit workspace to individual div (document) here.
# For each Div element with an XML:ID (should be each document)
for document in soup.findAll("div", {"xml:id":True}):
    # Get the document ID from the <div> element.
    documentID = list(document.attrs.values())[0]
    
    documentType = document.find("list", {"type" : "objectType"}).findChild(True, recursive=True).attrs["n"]
    #print("DEBUG Checking",documentID)
    # Check if the document has more than 0 recipients. If there are no recipients, there is no correspAction required.
    recipient = document.find("item", {"n":"recipient"})
    
    # Check if the document has an author.
    authorName = document.find("item", {"n":"author"})
    if authorName:
        authorName = authorName.contents[0]
    else:
        authorName = "No author"
        print("WARNING:",documentID,"suffered code 201881 no author found!")
        errors_found.append("INFO 201881 in "+str(documentID))
    # Attempt to divine the date or date range of the document. Assumes that each document only has 1 date (or 1 range).
    isDocumentUndated = document.find("item", {"n":"undated"})
    if isDocumentUndated:
        date = "s.d."
    else:
        isDocumentFromTo = document.find("date", {"from":True}) # Does the date element have a from assignment? 
        # Using "from" because PN1350 does not have a fromTo attr despite using fromTo. Uses "from", though. Works fine.
        if isDocumentFromTo: # If it does, and thus has a range (JK, No-MM_T1296 has FROM attr but not a TO attr.)
            doesDocumentHaveToDate = document.find("date", {"to":True})
            if doesDocumentHaveToDate:
                date = isDocumentFromTo['from']+"-"+isDocumentFromTo['to'] # Extract from and to dates. 
                #date = " ".join(date)
            else:
                date = isDocumentFromTo['from']
        elif not isDocumentFromTo: # If it doesn't:
            yearSent = document.find("date", {"type":"year","when":True}) # Check for year element
            monthSent = document.find("date", {"type":"month","when":True}) # Check for month element
            daySent = document.find("date", {"type":"day","when":True}) # Check for day element
            if yearSent:
                date = yearSent.attrs["when"]
                if monthSent: # Only look for a month if there's a year. That 1 letter with just month/day, tho...
                    M = re.sub('[-]', '', monthSent.attrs["when"]) # Strip the random '-' characters in here.
                    date+="-"+str(M) # Join month to year by YYYY-MM.
                    if daySent: # Only applies if there is a month AND a day. No point having a day if you don't have a month.
                        M = re.sub('[-]', '', daySent.attrs["when"]) # Strip the random '-' characters in here, too.
                        date+="-"+str(M) # Join month to year-month by YYYY-MM-DD.
            else:
                date = "s.d."
                print("WARNING:",documentID,"suffered code 301881 - no year found in a specific-year element. Expected in MM_N1071 and MM_N3734.")
                errors_found.append("INFO 301881 in "+str(documentID))
        else:
            print("WARNING:",documentID,"suffered error 301882 - catastrophic date error")
            errors_found.append("CRITICAL ERROR 301882 in "+str(documentID))


    # If there is a recipient, there exists a correspAction - one does naturally follow the other.
    if recipient: # If there are more than 0 recipients:
        if date != "s.d.":
            print(documentID+", dated",date)
        else:
            print(documentID+", undated")
        z=0
        recipientList = recipient.findChildren(True) # Get ALL children of the recipient item element. Might be 2+!
        for each in recipientList: # For every recipient:
            recipientName = str(each.contents[0]) # Assign a name
            if recipientName not in addresseesUnique:
                addresseesUnique.append(recipientName)
            recipientID = recipientList[z].attrs["target"] # Assign an ID
            if "institution" in recipientID:
                recipientType = "orgName"
            elif "person" in recipientID:
                recipientType = "persName"
            else:
                print("WARNING:",documentID,"suffered error 20191. Defaulted to person.")
                recipientType = "orgName"
                errors_found.append("WARNING 20191 in "+str(documentID))
            #if len(recipientList) > 1:
            #    print(z,"Multiple recipients. Primary:",recipientList[0],"with",recipientList[z])
            
            
            
            z+=1 # Yes - here, not after the following. We want z to start at 1.
            if len(recipientList) == 1: # Single-recipient code goes here
                print("From",authorName,"to",recipientType,recipientName,recipientID,"\n")
                #pass
            else: # Multi-recipient code goes here
                if z < len(recipientList):
                    print("From",authorName,"to",recipientType,recipientName,recipientID,"part",z,"/",len(recipientList))
                    #pass
                elif z == len(recipientList):
                    print("From",authorName,"to",recipientType,recipientID,"part",z,"/",len(recipientList),"\n")
                    #pass
                else: # If z is out of range in relation to recipientList:
                    print("WARNING:",documentID,"suffered error 30190.")
                    errors_found.append("30190/"+str(documentID))
        letterCount+=1
    else: # If document does not have a recipient, what do we do?
        #print(date,"by",authorName,"is a \""+str(documentType)+"\" with no recipient.")
        miscCount+=1
end = time.time()

All comments destroyed.
No-MM_N0025, dated 1912
From Edvard Munch to persName Uidentifisert kvinne person.xhtml?id=pe973 

No-MM_N0037, dated 1933-1934
From Edvard Munch to persName Jens Thiis person.xhtml?id=pe458 

No-MM_N0041, dated 1929
From Edvard Munch to persName Ragnar Hoppe person.xhtml?id=pe531 

No-MM_N0043, dated 1933-1940
From Edvard Munch to persName Jens Thiis person.xhtml?id=pe458 

No-MM_N0061, dated 1933
From Edvard Munch to persName Jens Thiis person.xhtml?id=pe458 

No-MM_N0090, dated 1939
From Edvard Munch to persName Harry Fett person.xhtml?id=pe124 part 1 / 2
From Edvard Munch to orgName institution.xhtml?id=i20 part 2 / 2 

No-MM_N0091, dated 1934-1940
From Edvard Munch to persName Uidentifisert mann person.xhtml?id=pe486 

No-MM_N0118, dated 1904
From Edvard Munch to persName Uidentifisert person person.xhtml?id=pe1199 

No-MM_N0120, dated 1890-03-22
From Edvard Munch to orgName Det kongelige Kirke- og Undervisningsdepartement institution.xhtml?id=i33 

No-MM_N

From Edvard Munch to persName Uidentifisert mann person.xhtml?id=pe486 

No-MM_N0529, undated
From Edvard Munch to persName Arnstein Arneberg person.xhtml?id=pe9 

No-MM_N0530, undated
From Edvard Munch to persName Uidentifisert mann person.xhtml?id=pe486 

No-MM_N0540, undated
From Edvard Munch to persName Uidentifisert person person.xhtml?id=pe1199 

No-MM_N0549, undated
From Edvard Munch to persName Johannes Roede person.xhtml?id=pe836 

No-MM_N0552, dated 1910-04-26
From Edvard Munch to persName Kai Christensen person.xhtml?id=pe504 

No-MM_N0553, dated 1896-1897
From Edvard Munch to persName Axel Heiberg person.xhtml?id=pe180 

No-MM_N0554, undated
From Edvard Munch to persName Uidentifisert person person.xhtml?id=pe1199 

No-MM_N0557, undated
From Edvard Munch to orgName Akers Ligningsvæsen, Akers Ligningsråd, Akers ligningskontor institution.xhtml?id=i2 

No-MM_N0558, undated
From Edvard Munch to orgName Akers Ligningsvæsen, Akers Ligningsråd, Akers ligningskontor institution.xh

No-MM_N0786, dated 1892-11-17
From Edvard Munch to persName Karen Bjølstad person.xhtml?id=pe495 

No-MM_N0787, dated 1892-11-26
From Edvard Munch to persName Karen Bjølstad person.xhtml?id=pe495 

No-MM_N0788, dated 1892-12
From Edvard Munch to persName Karen Bjølstad person.xhtml?id=pe495 

No-MM_N0789, dated 1892
From Edvard Munch to persName Karen Bjølstad person.xhtml?id=pe495 

No-MM_N0790, dated 1893-01-20
From Edvard Munch to persName Inger Munch person.xhtml?id=pe348 

No-MM_N0791, dated 1893-02-25
From Edvard Munch to persName Karen Bjølstad person.xhtml?id=pe495 

No-MM_N0792, dated 1893-1893
From Edvard Munch to persName Karen Bjølstad person.xhtml?id=pe495 

No-MM_N0793, dated 1893
From Edvard Munch to persName Karen Bjølstad person.xhtml?id=pe495 

No-MM_N0794, dated 1893-05-26
From Edvard Munch to persName Karen Bjølstad person.xhtml?id=pe495 

No-MM_N0795, dated 1893-06-18
From Edvard Munch to persName Karen Bjølstad person.xhtml?id=pe495 

No-MM_N0796, dated 1893
From 

No-MM_N0947, dated 1908-01-18
From Edvard Munch to persName Karen Bjølstad person.xhtml?id=pe495 

No-MM_N0948, dated 1909-02-26
From Edvard Munch to persName Karen Bjølstad person.xhtml?id=pe495 

No-MM_N0949, dated 1909-04-11
From Edvard Munch to persName Karen Bjølstad person.xhtml?id=pe495 

No-MM_N0950, dated 1909-04-15
From Edvard Munch to persName Karen Bjølstad person.xhtml?id=pe495 

No-MM_N0951, dated 1909-05-11
From Edvard Munch to persName Karen Bjølstad person.xhtml?id=pe495 

No-MM_N0952, dated 1909-05-18
From Edvard Munch to persName Karen Bjølstad person.xhtml?id=pe495 

No-MM_N0953, dated 1909
From Edvard Munch to persName Karen Bjølstad person.xhtml?id=pe495 

No-MM_N0954, dated 1909
From Edvard Munch to persName Karen Bjølstad person.xhtml?id=pe495 

No-MM_N0955, dated 1909-06-20
From Edvard Munch to persName Karen Bjølstad person.xhtml?id=pe495 

No-MM_N0956, dated 1909-07-14
From Edvard Munch to persName Karen Bjølstad person.xhtml?id=pe495 

No-MM_N0957, dated 190

From Edvard Munch to persName Inger Munch person.xhtml?id=pe348 

No-MM_N1116, dated 1926-03-02
From Edvard Munch to persName Inger Munch person.xhtml?id=pe348 

No-MM_N1117, dated 1926-06-03
From Edvard Munch to persName Inger Munch person.xhtml?id=pe348 

No-MM_N1118, dated 1926
From Edvard Munch to persName Inger Munch person.xhtml?id=pe348 

No-MM_N1119, dated 1926-09-23
From Edvard Munch to persName Inger Munch person.xhtml?id=pe348 

No-MM_N1120, dated 1926-11-20
From Edvard Munch to persName Inger Munch person.xhtml?id=pe348 

No-MM_N1121, dated 1923
From Edvard Munch to persName Inger Munch person.xhtml?id=pe348 

No-MM_N1122, dated 1927-01-14
From Edvard Munch to persName Inger Munch person.xhtml?id=pe348 

No-MM_N1123, dated 1927-02-28
From Edvard Munch to persName Inger Munch person.xhtml?id=pe348 

No-MM_N1124, dated 1927-03-04
From Edvard Munch to persName Inger Munch person.xhtml?id=pe348 

No-MM_N1125, dated 1927-03-07
From Edvard Munch to persName Inger Munch person.xht

...

PN0721, dated 1909-03-09
From Edvard Munch to persName Jappe Nilssen person.xhtml?id=pe366 

PN0722, dated 1909-03-12
From Edvard Munch to persName Jappe Nilssen person.xhtml?id=pe366 

PN0723, dated 1909-03-13
From Edvard Munch to persName Jappe Nilssen person.xhtml?id=pe366 

PN0724, dated 1909-03-24
From Edvard Munch to persName Jappe Nilssen person.xhtml?id=pe366 

PN0725, dated 1909-03-27
From Edvard Munch to persName Jappe Nilssen person.xhtml?id=pe366 

PN0726, dated 1909-04-05
From Edvard Munch to persName Jappe Nilssen person.xhtml?id=pe366 

PN0727, dated 1909-04-08
From Edvard Munch to persName Jappe Nilssen person.xhtml?id=pe366 

PN0728, dated 1909-04-12
From Edvard Munch to persName Jappe Nilssen person.xhtml?id=pe366 

PN0729, dated 1909-04-12
From Edvard Munch to persName Jappe Nilssen person.xhtml?id=pe366 

PN0730, dated 1909-04-20
From Edvard Munch to persName Jappe Nilssen person.xhtml?id=pe366 

PN0731, dated 1909-10-24
From Edvard Munch to persName Jappe Nilssen p

From Edvard Munch to persName Thilo Schoder person.xhtml?id=pe573 

PN0892, dated 1934-01-14
From Edvard Munch to persName Thilo Schoder person.xhtml?id=pe573 

PN0893, dated 1934-01-26
From Edvard Munch to persName Thilo Schoder person.xhtml?id=pe573 

PN0894, dated 1944-05-25
From Edvard Munch to persName Thilo Schoder person.xhtml?id=pe573 

PN0895, dated 1897-07-22
From Edvard Munch to persName Ole Smith Housken person.xhtml?id=pe208 

PN0896, dated 1934-02-09
From Edvard Munch to persName Ole Antonsen  Thingstad person.xhtml?id=pe459 

PN0897, dated 1929-01-14
From Edvard Munch to persName Axel Thoresen person.xhtml?id=pe596 

PN0898, dated 1897-11-30
From Edvard Munch to persName Agnes Thorsen person.xhtml?id=pe597 

PN0899, undated
From Edvard Munch to persName Ingse Vibe person.xhtml?id=pe466 

PN0900, undated
From Edvard Munch to persName Ingse Vibe person.xhtml?id=pe466 

PN0901, undated
From Edvard Munch to persName Ingse Vibe person.xhtml?id=pe466 

PN0902, undated
From Edv

PN0994, dated 1909-10-29
From Edvard Munch to persName Daniel Jacobson person.xhtml?id=pe226 

No-MM_T1992, undated
From Edvard Munch to persName Erik Werenskiold person.xhtml?id=pe606 

No-MM_T1908, undated
From Edvard Munch to persName Uidentifisert mann person.xhtml?id=pe486 

No-MM_T2181, undated
From Edvard Munch to persName Marcus Irgens person.xhtml?id=pe223 

No-MM_N1652, dated 1930-1933
From Edvard Munch to persName Haakon Mahrt person.xhtml?id=pe315 

No-MM_T2810, dated 1890-01-24
From Edvard Munch to persName Karen Bjølstad person.xhtml?id=pe495 

PN0995, dated 1909-03-10
From Edvard Munch to persName Ragnvald Væring person.xhtml?id=pe1027 

No-MM_T2897, undated
From Edvard Munch to persName Arnstein Arneberg person.xhtml?id=pe9 

No-MM_N3677, dated 1918-06-13
From Edvard Munch to persName Edvard Munch person.xhtml?id=pe627 

No-MM_N3678, dated 1889
From Edvard Munch to persName Aase  Nørregaard person.xhtml?id=pe368 

No-MM_N3679, dated 1893-03-16
From Edvard Munch to persN

PN1102, dated 1938
From Edvard Munch to orgName The London Gallery institution.xhtml?id=i57 

PN1103, dated 1906-04-15
From Edvard Munch to persName Frederick Delius person.xhtml?id=pe88 

PN1104, dated 1904
From Edvard Munch to orgName Kunstverein Jena e.V. (Jenaer Kunstverein) institution.xhtml?id=i227 

PN1105, undated
From Edvard Munch to orgName Kunstverein Jena e.V. (Jenaer Kunstverein) institution.xhtml?id=i227 

PN1106, undated
From Edvard Munch to orgName Kunstverein Jena e.V. (Jenaer Kunstverein) institution.xhtml?id=i227 

PN1107, dated 1910-01-12
From Edvard Munch to persName Jens Willumsen person.xhtml?id=pe608 

PN1108, undated
From Edvard Munch to orgName F. Bruckmann H.-G. institution.xhtml?id=i7 

PN1109, dated 1924
From Edvard Munch to persName Julius Meier-Graefe person.xhtml?id=pe323 

PN1110, dated 1912-03-30
From Edvard Munch to persName Herwarth Walden person.xhtml?id=pe1024 

PN1111, dated 1912-02-16
From Edvard Munch to persName Herwarth Walden person.xhtml?id=

From Edvard Munch to persName Bjørnstjerne Bjørnson person.xhtml?id=pe44 part 1 / 2
From Edvard Munch to orgName institution.xhtml?id=i88 part 2 / 2 

PN1241, dated 1896
From Edvard Munch to persName Erik Lie person.xhtml?id=pe294 

No-MM_N0395, dated 1918-09
From Edvard Munch to persName Christian Axel  Dahl person.xhtml?id=pe1333 

No-MM_N0396, undated
From Edvard Munch to orgName Vækerø politi institution.xhtml?id=i299 

PN1242, dated 1911-01-21
From Edvard Munch og  to persName Cally Monrad person.xhtml?id=pe345 

PN1244, dated 1903-03-24
From Edvard Munch to persName Frederick Delius person.xhtml?id=pe88 

PN1245, dated 1908-08-08
From Edvard Munch to persName Eberhard Grisebach person.xhtml?id=pe152 

PN1246, dated 1908-08-18
From Edvard Munch to persName Eberhard Grisebach person.xhtml?id=pe152 

PN1247, dated 1909-12-23
From Edvard Munch to persName Eberhard Grisebach person.xhtml?id=pe152 

PN1248, dated 1914-05-20
From Edvard Munch to persName Andrea Munch-Ellingsen person.xh

In [106]:
print("Processed",letterCount,"letters (with recipients) and",miscCount,"other documents (without recipients) in",round(end - start,1),"seconds.")
if len(errors_found) > 0:
    i = 0
    print(len(errors_found),"data warnings and errors, listed as INFO, WARNING, and ERROR in order of severity.")
    for error in errors_found:
        i+=1
        if "201881" in error:
            print(i,error,"- Document has no author. Registered as \"No author\".")
        elif "301881" in error:
            print(i,error,"- Document has a specific date, but no year. Document has been given \"undated\" status.")
        elif "301882" in error:
            print(i,error,"- Catastrophic failure in date format or harvesting. The script was not designed for this.")
        elif "30190" in error:
            print(i,error,"- Catastrophic failure in recipient list processing. I don't think the script will run to this point with such an error.")
        elif "20191" in error:
            print(i,error,"- The recipient is not a person or an organization. Suggests error in reference XMLURI. Defaulted to person.")
else:
    print("No warnings or errors found.")

Processed 4290 letters (with recipients) and 1153 other documents (without recipients) in 6.5 seconds.
3 warnings and errors. 
1 INFO 301881 in No-MM_N1071 - Document has a specific date, but no year. Document has been given "undated" status.
2 INFO 201881 in No-MM_N2099 - Document has no author. Registered as "No author".
3 INFO 301881 in No-MM_N3734 - Document has a specific date, but no year. Document has been given "undated" status.


In [107]:
soup.find("div", {"xml:id" : "No-MM_N0559"})

<div xml:id="No-MM_N0559">
            MM N 559
            <list type="proveniens">
<item n="ownerMsSig">MM N 559</item>
<item n="owner">Munchmuseet</item>
</list>
<list type="description">
<item n="author">Edvard Munch</item>
<item n="recipient">
<ref target="person.xhtml?id=pe836">Johannes Roede</ref>
</item>
<item n="sort">Roede, Johannes </item>
<item><list type="objectType"><item n="draft">utkast</item></list></item>
<item><list type="date"><item n="undated">Ikke datert</item></list></item>
<item n="language">norsk</item>
</list>
<list type="physDescription">
<item n="paperType">skrivepapir</item>
<item n="measures">275×215 mm (h×b)</item>
</list>
</div>

### CMIF

https://correspsearch.net/en/documentation.html

/correspAction/@type == correspAction element with attribute type="xyz"

/correspAction/persName == correspAction element with persName child element

@X == attribute of element

*Each letter, postcard - document - that is to be described features its own **correspDesc element**. *There are as many correspDescs as there are items. A particular correspDesc element in CMI format is more restrictive and reduced with regard to its vocabulary than the TEI Guidlines generally allow. This enables interchange between the respective TEI documents.*

for each in letters:
    create correspDesc wrapper
    
<correspDesc>
    <correspAction type="sent">
        <persName ref="VIAFetc url">NAME</>
        <placeName ref="Geonames url">NAME</>
    <correspAction type="received">
        <persName ref="url">NAME</>
        <placeName ref="Geonames url">NAME</>

### Mapping tags
*Italics* == Tag is category/folder only, does not contain text in itself

#### TEI-Header (metadata)
1. *Titlestmt* {Title, Editor(email)}
2. *Publicationstmt* {*Publisher* (Ref @target), idno@url, date@when, *Availability*(licence@target)}
3. *Sourcedesc* {Bibl@type@xml:id} - type="online" xml:id="cmifUid"

The header mostly features direct correlation, or items where the program will directly inject new information.

Now, because nothing is easy, the example file is just all TEI header including the letters it wants to describe. There is a body tag with a random \<p/>, which just serves absolutely no purpose. Why?

#### "profileDesc" (data)
1. correspDesc @key @ref @source {correspAction @type (persname @ref, placename @ref, *date @when*), correspAction @type (persname @ref, placename @ref, *date @when*)}

Dates need to be YYYY-MM-DD, dropping DD and/or MM if required. Unknown dates should be skipped as per CMIF documentation. 
